# Time series in the VO -- how to be not seen #

## The use case ## 

Around March 2023 a collegue and VO expert approach me with an actually simple VO use case: how to find TESS lightcurves in the VO with VO tools. What at the first glance seemed like an easy and simple task, very soon turned into something very different. 
Here I will present the steps we did to solve this question and hope to demonstrate that this certainly is not a good way to for non VO experts to follow.

## The first approach ##
The first approach to find data in the VO of course is to send a query to the VO registry. So for TESS lightcurves the first step would be to search for TESS data. 

In [1]:
import pyvo

results=pyvo.registry.search(keywords='TESS')

print (results)

<Table length=341>
                  ivoid                    ...
                                           ...
                  object                   ...
------------------------------------------ ...
           ivo://archive.stsci.edu/caomtap ...
ivo://archive.stsci.edu/catalogs/tessinput ...
            ivo://archive.stsci.edu/cs/tic ...
                   ivo://cadc.nrc.ca/argus ...
                   ivo://cds.vizier/ii/366 ...
                    ivo://cds.vizier/iv/38 ...
                    ivo://cds.vizier/iv/39 ...
            ivo://cds.vizier/j/a+a/569/a21 ...
            ivo://cds.vizier/j/a+a/600/a30 ...
                                       ... ...
         ivo://cds.vizier/j/mnras/513/6042 ...
         ivo://cds.vizier/j/mnras/515/3212 ...
         ivo://cds.vizier/j/mnras/519/4699 ...
      ivo://cds.vizier/j/other/coska/51.78 ...
  ivo://cds.vizier/j/other/newa/101.102022 ...
     ivo://cds.vizier/j/other/raa/23.c5016 ...
         ivo://cds.vizier/j/pasp/131/c440

Well, 341 results are a bit overwhelming which on the one hand is good news, because it seems there is a lot of data available, and we have to narrow down our search. So an intuitive way would be to add something to the keywords -- though of course we (as: VO guys) are very well aware that this is not the proper way, it's the *obvious* way for VO users. So we went down the path:

In [2]:
results=pyvo.registry.search(keywords='TESS lightcurves')
print (results)

<Table length=6>
             ivoid              ...
                                ...
             object             ...
------------------------------- ...
 ivo://cds.vizier/j/a+a/635/a13 ...
 ivo://cds.vizier/j/a+a/655/a66 ...
ivo://cds.vizier/j/a+a/664/a162 ...
  ivo://cds.vizier/j/aj/162/127 ...
 ivo://cds.vizier/j/apjs/245/29 ...
 ivo://cds.vizier/j/apjs/259/33 ...


Unfortunately none of the results in Vizier actually provide the TESS lightcurves, so our query was too narrow, but the next best term 'time series' returns a similar result:

In [3]:
results=pyvo.registry.search(keywords='TESS time series')

for i in results:
    print (i['ivoid'])

ivo://cds.vizier/j/a+a/619/l10
ivo://cds.vizier/j/a+a/625/l13
ivo://cds.vizier/j/a+a/630/a106
ivo://cds.vizier/j/a+a/638/a108
ivo://cds.vizier/j/a+a/639/a35
ivo://cds.vizier/j/a+a/643/a110
ivo://cds.vizier/j/a+a/660/a86
ivo://cds.vizier/j/a+a/664/a162
ivo://cds.vizier/j/a+a/666/a155
ivo://cds.vizier/j/a+a/667/a63
ivo://cds.vizier/j/a+a/668/a158
ivo://cds.vizier/j/a+a/671/l8
ivo://cds.vizier/j/aca/70/1
ivo://cds.vizier/j/aca/72/31
ivo://cds.vizier/j/aj/158/243
ivo://cds.vizier/j/aj/161/170
ivo://cds.vizier/j/aj/161/171
ivo://cds.vizier/j/aj/161/194
ivo://cds.vizier/j/aj/161/46
ivo://cds.vizier/j/aj/162/150
ivo://cds.vizier/j/aj/163/19
ivo://cds.vizier/j/aj/164/216
ivo://cds.vizier/j/aj/164/70
ivo://cds.vizier/j/apjs/245/13
ivo://cds.vizier/j/apjs/259/50
ivo://cds.vizier/j/mnras/473/2004
ivo://cds.vizier/j/mnras/478/2676
ivo://cds.vizier/j/mnras/496/5423


As time series are observational data we easily found the right way to figure it out by using obscore:

In [4]:
results=pyvo.registry.search(keywords='TESS', datamodel='obscore')
print (results)

<Table length=2>
             ivoid                   res_type     ...  intf_types  intf_roles
                                                  ...                        
             object                   object      ...    object      object  
------------------------------- ----------------- ... ------------ ----------
ivo://archive.stsci.edu/caomtap vs:catalogservice ... vs:paramhttp        std
        ivo://cadc.nrc.ca/argus vs:catalogservice ... vs:paramhttp        std


In [5]:
for svc in results:
    obsc_service = pyvo.dal.TAPService(svc.access_url)
    obsc_result = obsc_service.search(
        """SELECT * FROM ivoa.Obscore
        WHERE dataproduct_type='timeseries'
        AND CONTAINS(POINT('ICRS', 073.3813019796800, -06.6957980314600), s_region)=1
        AND obs_collection='TESS'""")
#    obsc_result.broadcast_samp('topcat')
    print (svc.short_name,"\n", obsc_result, "\n")

STScI CAOMTAP 
 <Table length=12>
dataproduct_type calib_level obs_collection ... facility_name instrument_name
                                            ...                              
     object         int32        object     ...     object         object    
---------------- ----------- -------------- ... ------------- ---------------
      timeseries           3           TESS ...     NASA/Ames      Photometer
      timeseries           3           TESS ...     NASA/Ames      Photometer
      timeseries           3           TESS ...     NASA/Ames      Photometer
      timeseries           3           TESS ...     NASA/Ames      Photometer
      timeseries           3           TESS ...     NASA/Ames      Photometer
      timeseries           3           TESS ...     NASA/Ames      Photometer
      timeseries           3           TESS ...     NASA/Ames      Photometer
      timeseries           3           TESS ...     NASA/Ames      Photometer
      timeseries           3  

Sending the whole thing to topcat we easily see that the results from CADC even contain datalinks to the data products -- which lead to the time series on the services of STSCI. 
This might explain though, why using google to search for "TESS light curves" will lead to the TESS documention of STSCI, but in now way ever points to CADC. 

## How stupid am I ?##
Apparently I fail at finding TESS light curves with VO tools only, unless relyin on obscore -- which is a cool standard, but for really advanced VO users. Yet, it puzzled me and I really felt like I was stupid and missing something (though in good company of Ada, and the thought, that my stupidity was on the same level as Adas was very soothing.) Finding TESS light curves and accessing them was so hard compared to the ones of Gaia. 

Is it, thought ? Actually, I never searched for Gaia light curves. I knew where to find them, because I use to hang out with the right crowd of cool kids (the IVOA folks), so I never needed to search for Gaia light curves. Well, let's test that:

In [6]:
results=pyvo.registry.search(keywords='Gaia')

print (results)

<Table length=1307>
                   ivoid                    ...
                                            ...
                   object                   ...
------------------------------------------- ...
     ivo://archive.stsci.edu/catalogs/atlas ...
   ivo://archive.stsci.edu/catalogs/gaiadr1 ...
   ivo://archive.stsci.edu/catalogs/gaiadr2 ...
     ivo://archive.stsci.edu/catalogs/ucac5 ...
  ivo://astronet.ru/cas/gaiadr2-gaia_source ...
                  ivo://cds.vizier/b/pollux ...
                     ivo://cds.vizier/i/324 ...
                     ivo://cds.vizier/i/325 ...
                     ivo://cds.vizier/i/331 ...
                                        ... ...
                     ivo://svo.cab/cat/wdw2 ...
                     ivo://svo.cab/cat/wdw3 ...
    ivo://uni-heidelberg.de/gaia/conesearch ...
           ivo://uni-heidelberg.de/gaia/tap ...
 ivo://uni-heidelberg.de/gaiadr1/conesearch ...
 ivo://uni-heidelberg.de/gaiadr2/conesearch ...
ivo://uni-heidelberg

In [7]:
results=pyvo.registry.search(keywords='Gaia lightcurves')
print (results)

<Table length=5>
             ivoid              ...
                                ...
             object             ...
------------------------------- ...
 ivo://cds.vizier/j/a+a/620/a91 ...
 ivo://cds.vizier/j/a+a/649/a98 ...
 ivo://cds.vizier/j/a+a/661/a44 ...
ivo://cds.vizier/j/a+a/664/a162 ...
  ivo://org.gavo.dc/gaia/q2/ssa ...


In [8]:
results=pyvo.registry.search(keywords='Gaia time series')

for i in results:
    print (i['ivoid'])

ivo://cds.vizier/j/a+a/587/a112
ivo://cds.vizier/j/a+a/619/a51
ivo://cds.vizier/j/a+a/619/l10
ivo://cds.vizier/j/a+a/622/a60
ivo://cds.vizier/j/a+a/623/a110
ivo://cds.vizier/j/a+a/623/a83
ivo://cds.vizier/j/a+a/627/a135
ivo://cds.vizier/j/a+a/641/a51
ivo://cds.vizier/j/a+a/649/a7
ivo://cds.vizier/j/a+a/656/a66
ivo://cds.vizier/j/a+a/657/a131
ivo://cds.vizier/j/a+a/657/a31
ivo://cds.vizier/j/a+a/664/a162
ivo://cds.vizier/j/a+a/667/a83
ivo://cds.vizier/j/a+a/668/a59
ivo://cds.vizier/j/a+a/671/a50
ivo://cds.vizier/j/a+a/672/a31
ivo://cds.vizier/j/a+a/672/a69
ivo://cds.vizier/j/aj/153/154
ivo://cds.vizier/j/aj/153/204
ivo://cds.vizier/j/aj/158/77
ivo://cds.vizier/j/aj/159/114
ivo://cds.vizier/j/aj/160/220
ivo://cds.vizier/j/aj/161/170
ivo://cds.vizier/j/aj/162/100
ivo://cds.vizier/j/apj/835/173
ivo://cds.vizier/j/apj/844/66
ivo://cds.vizier/j/apj/884/20
ivo://cds.vizier/j/apj/888/73
ivo://cds.vizier/j/apj/898/173
ivo://cds.vizier/j/apj/909/115
ivo://cds.vizier/j/apj/911/51
ivo://cds.vizier

In [9]:
results=pyvo.registry.search(keywords='Gaia dr3')
for i in results:
    print (i['ivoid'])

ivo://cds.vizier/i/350
ivo://cds.vizier/i/353
ivo://cds.vizier/i/354
ivo://cds.vizier/i/355
ivo://cds.vizier/i/356
ivo://cds.vizier/i/357
ivo://cds.vizier/i/358
ivo://cds.vizier/i/359
ivo://cds.vizier/i/360
ivo://cds.vizier/ii/374
ivo://cds.vizier/j/a+a/617/a135
ivo://cds.vizier/j/a+a/624/a13
ivo://cds.vizier/j/a+a/638/a76
ivo://cds.vizier/j/a+a/653/a160
ivo://cds.vizier/j/a+a/656/a110
ivo://cds.vizier/j/a+a/659/a167
ivo://cds.vizier/j/a+a/660/a34
ivo://cds.vizier/j/a+a/661/a103
ivo://cds.vizier/j/a+a/662/a40
ivo://cds.vizier/j/a+a/664/a109
ivo://cds.vizier/j/a+a/666/a128
ivo://cds.vizier/j/a+a/666/l4
ivo://cds.vizier/j/a+a/667/a74
ivo://cds.vizier/j/a+a/668/a99
ivo://cds.vizier/j/a+a/669/a139
ivo://cds.vizier/j/a+a/669/a91
ivo://cds.vizier/j/a+a/670/a102
ivo://cds.vizier/j/a+a/670/a75
ivo://cds.vizier/j/a+a/670/l2
ivo://cds.vizier/j/a+a/671/a149
ivo://cds.vizier/j/a+a/672/a166
ivo://cds.vizier/j/a+a/672/a183
ivo://cds.vizier/j/a+a/672/a31
ivo://cds.vizier/j/a+a/672/a65
ivo://cds.vizie